In [1]:
import numpy as np
from pickle import dump
from datetime import datetime
import plotly.graph_objects as go
from quantfreedom import dl_ex_candles
from quantfreedom.helpers.helper_funcs import np_lb_one
from quantfreedom.indicators.tv_indicators import rsi_tv

%load_ext autoreload
%autoreload 2

In [2]:
candles = dl_ex_candles(
    exchange="mufex",
    symbol="BTCUSDT",
    timeframe="5m",
    since_datetime=datetime(2023, 10, 11),
    until_datetime=datetime(2023, 12, 5),
)
with open("../dbs/oct_dec_candles.pkl", "wb") as f:
    dump(candles, f)

In [3]:
rsi_length = 14
below_rsi_cur = 45
below_rsi_p = 30
below_rsi_pp = 35

In [4]:
rsi = rsi_tv(
    source=candles.candle_close_prices,
    length=rsi_length,
)

rsi = np.around(rsi, 1)

rsi_lb = np_lb_one(
    arr=rsi,
    lookback=2,
)

p_rsi = rsi_lb[:, 0]
pp_rsi = rsi_lb[:, 1]

falling = pp_rsi > p_rsi
rising = p_rsi < rsi

is_below_cur = rsi < below_rsi_cur
is_below_p = p_rsi < below_rsi_p
is_below_pp = pp_rsi < below_rsi_pp

entries = is_below_cur & is_below_p & is_below_pp & falling & rising
entry_signals = np.where(entries, rsi, np.nan)

exit_prices = np.full_like(rsi, np.nan)

In [5]:
fig = go.Figure()
datetimes = candles.candle_open_datetimes

In [6]:
fig.add_scatter(
    x=datetimes,
    y=rsi,
    name="rsi",
    line_color="yellow",
)

In [7]:
fig.add_scatter(
    x=datetimes,
    y=entry_signals,
    mode="markers",
    name="entries",
    marker=dict(
        size=12,
        symbol="circle",
        color="#00F6FF",
        line=dict(
            width=1,
            color="DarkSlateGrey",
        ),
    ),
)

In [8]:
fig.add_hline(
    y=below_rsi_cur,
    opacity=0.3,
    line_color="red",
)

In [9]:
fig.update_layout(
    height=500,
    xaxis_rangeslider_visible=False,
    title=dict(
        x=0.5,
        text="Long Signals",
        xanchor="center",
        font=dict(
            size=50,
        ),
    ),
)